## Classes and Objects

Let's try to implement our first class

In [1]:
class aggregate {
    short s = 4;
    unsigned int i = 1u<<16;
    double x = 2.0;
};

In [2]:
#include <iostream>

int main() {
    aggregate agg;
    std::cout << "s = " << agg.s << std::endl;
    std::cout << "i = " << agg.i << std::endl;
}

input_line_9:3:32: error: 's' is a private member of '__cling_N52::aggregate'
    std::cout << "s = " << agg.s << std::endl;
                               ^
input_line_7:2:11: note: implicitly declared private here
    short s = 4;
          ^
input_line_9:4:32: error: 'i' is a private member of '__cling_N52::aggregate'
    std::cout << "i = " << agg.i << std::endl;
                               ^
input_line_7:3:18: note: implicitly declared private here
    unsigned int i = 1u<<16;
                 ^


Interpreter Error: 

That did not work. Why?

Because object-oriented programming is also about **encapsulation**. By making certain attributes (data members) and methods (member functions) invisible to the outside, we
  - can enhance safety: better control over the state of an object
  - make sure that the internal implementation of the class can be changed without breaking outside code  

In C++ we have three levels of access:
  - **public** = any one has access 
  - **private** = only the class itself has access
  - **protected** = the class and its children have access
  
The difference between a struct and a class lies in their default setting

|            | class | struct |
|:----------:|:-----:|:------:|
| default is:|private| public |

In [1]:
class aggregate {
  
  double x;         // private by default
    
public:
    
  short s = 4;
  unsigned int i = 1u<<16;

};

struct combo {
  
  int a;            // public by default
    
private:
  int internal;     // not accessible from outside

};

In [2]:
#include <iostream>

int main() {
  aggregate agg;
  std::cout << "s = " << agg.s << std::endl;
  std::cout << "i = " << agg.i << std::endl;

  combo s;
  s.a = 7;
}

main();

s = 4
i = 65536


An **object** is an instance of a class; different objects are different entities.

In [3]:
int main() {
    
    aggregate a, b, c;
    
    a.s = 1;
    b.s = 2;
    c.s = 3;
    
    std::cout << "a's short has a value of " << a.s << '\n'
              << "b's short has a value of " << b.s << '\n'
              << "c's short has a value of " << c.s << std::endl;
    
    a = c;
    std::cout << "now a.s = " << a.s << std::endl;
}

In [4]:
main();

a's short has a value of 1
b's short has a value of 2
c's short has a value of 3
now a.s = 3


### Constructors

- Our class *aggregate* used *default member initializers* for setting initial values for its data members.
- This is one possibility. The other is to use a *constructor* and a *member initializer list*.
- Constructors are also required, if we want to run some start-up code as part of object creation.

In [6]:
#include <iostream>

class myClass{
    
    public:
        myClass() : memb_(0) {
            std::cout << "An instance of myClass was generated."
                      << " memb_ = " << memb_ << std::endl;
        }
    
    private:
        int memb_; // some people adhere to the convention of marking data members by a trailing "_"
}

In [7]:
int main() {
    myClass myObj;
}

main();

An instance of myClass was generated. memb_ = 0


#### Multiple Constructors
C++ allows to overload functions. One can use this to implement different constructors.

In [8]:
class myClass{
    
    public:
        myClass() : memb_(0) {
            std::cout << "An instance of myClass was generated."
                      << " memb_ = " << memb_ << std::endl;
        }
    
        myClass( int member ) : memb_(member) {
            std::cout << "An instance of myClass was generated."
                      << " memb_ = " << memb_ << std::endl;
        }
    
    private:
        int memb_;
}

In [9]:
int main() {
    myClass myObj1;
    myClass myObj2( 5 );
}

main();

An instance of myClass was generated. memb_ = 0
An instance of myClass was generated. memb_ = 5


#### Constructor Delegation

In the example above the body of both constructors is identical. Such a code duplication is, of course, not nice and in violation of the **D**on't **R**epeat **Y**ourself principle. We can avoid this by using **constructor delegation**.

In [10]:
#include <iostream>

class myClass{
    
    public:
        myClass( int member ) : memb_(member) {
            std::cout << "An instance of myClass was generated."
                      << " memb_ = " << memb_ << std::endl;
        }

        myClass() : myClass(0) {}
        
    private:
        int memb_;
};

#### Cleaning up: Destructors
When an object goes out of scope and is destroyed we might want or need to do some housekeeping. For this we can implement a destructor.

In [12]:
#include <iostream>

class VerboseClass{
    
    public:
        // c'tor
        VerboseClass() {
            std::cout << "An instance of VerboseClass was generated." << std::endl;
        }

        // d'tor
        ~VerboseClass() {
            std::cout << "An instance of VerboseClass was destroyed.\n" << std::endl;
        }
};

In [13]:
int main() {
    for( int k = 0; k < 3; k++ ) {
        VerboseClass talky;
    }
}

main();

An instance of VerboseClass was generated.
An instance of VerboseClass was destroyed.

An instance of VerboseClass was generated.
An instance of VerboseClass was destroyed.

An instance of VerboseClass was generated.
An instance of VerboseClass was destroyed.



#### Small Project: A Vector Class for Linear Algebra
Tasks:
- We want to implement a class that represents a vector entity from linear algebra.
- The size of the vector should be selectable at object creation -> need to allocate memory dynamically.
- Access to vector entries should be 1-based -> operator overloading.
- Implement simple methods, such as
  - scaling vector with a constant
  - adding two vectors together
  - compute the Euclidean inner product of two vectors

In [14]:
// --------------------------------------
//  Start with the skeleton of the class
// --------------------------------------

#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( !dim_ == 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = "
                      << dim_ << std::endl;
        }

        // Don't allow the default constructor
        // [prior to C++11 you would have solved this by making it private]
        VectorClass() = delete;

    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector
};

In [15]:
int main() {
    VectorClass myVec( 420 );
}

In [16]:
main();

An instance of VectorClass was generated. dim_ = 420


Our implementation is **missing an essential piece**? What could that be?

In [19]:
// --------------------------------------
//  Start with the skeleton of the class
// --------------------------------------

#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( dim_ > 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = "
                      << dim_ << std::endl;
        }

        // Don't allow the default constructor
        // [prior to C++11 you would have solved this by making it private]
        VectorClass() = delete;
    
        // We need to implement a destructor to free the dynamic memory again,
        // otherwise we easily produce memory leaks
        ~VectorClass() {
            delete[] vec_;
            std::cout << "An instance of VectorClass was destroyed and "
                      << dim_ * sizeof(double)
                      << " bytes freed." << std::endl;
        }

    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector
};

In [20]:
int main() {
    VectorClass myVec( 10 );
}

main();

An instance of VectorClass was generated. dim_ = 10
An instance of VectorClass was destroyed and 80 bytes freed.


Our VectorClass is currently pretty useless, since we cannot manipulate the values of the vector entries. Making vec_ public would break encapsulation. Instead let's
- overload the [ ] for providing one-based access
- add a getter method for the dimension
- add a member function to pretty-print the vector's entries

In [22]:
#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( dim_ > 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = "
                      << dim_ << std::endl;
        }

        // Don't allow the default constructor
        // [prior to C++11 you would have solved this by making it private]
        VectorClass() = delete;
    
        // We need to implement a destructor to free the dynamic memory again,
        // otherwise we easily produce memory leaks
        ~VectorClass() {
            delete[] vec_;
            std::cout << "An instance of VectorClass was destroyed and "
                      << dim_ * sizeof(double)
                      << " bytes freed." << std::endl;
        }

        // provide access to the vector's dimension
        unsigned int getDim() { return dim_; }
    
        // overload the [] for accessing individual entries
        double& operator[] ( unsigned int index ) {
            assert( index != 0 && index <= dim_ );
            return vec_[index-1];
        }

        // pretty print vector to given output stream
        void print( std::ostream& os ) {
            os << "(";
            for( unsigned int k = 0; k < dim_-1; k++ ) {
                os << vec_[k] << ", ";
            }
            os << vec_[dim_-1] << ")" << std::endl;
        }
    
    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector

};

In [27]:
// Let's test our extended class

int main() {
    
    VectorClass myVec( 3 );
    
    myVec[ 1 ] = 3.0;
    myVec[ 2 ] = 2.0;
    myVec[ 3 ] = 1.0;
    
    std::cout << "Our vector has dimension " << myVec.getDim()
              << " and entries: ";
    myVec.print( std::cout );
}

main();

An instance of VectorClass was generated. dim_ = 3
Our vector has dimension 3 and entries: (3, 2, 1)
An instance of VectorClass was destroyed and 24 bytes freed.


**What is left on our todo-list?**
Implement simple methods, such as
  - scaling vector with a constant
  - adding two vectors together
  - compute the Euclidean inner product of two vectors

In [31]:
%%file VectorClass.cpp

#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( dim_ > 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = "
                      << dim_ << std::endl;
        }

        // Don't allow the default constructor
        // [prior to C++11 you would have solved this by making it private]
        VectorClass() = delete;
    
        // We need to implement a destructor to free the dynamic memory again,
        // otherwise we easily produce memory leaks
        ~VectorClass() {
            delete[] vec_;
            std::cout << "An instance of VectorClass was destroyed and "
                      << dim_ * sizeof(double)
                      << " bytes freed." << std::endl;
        }

        // provide access to the vector's dimension
        unsigned int getDim() { return dim_; }
    
        // overload the [] for accessing individual entries
        double& operator[] ( unsigned int index ){
            assert( index != 0 && index <= dim_ );
            return vec_[index-1];
        }

        // pretty print vector to given output stream (default will be std::cout)
        void print( std::ostream &os = std::cout ) {
            os << "(";
            for( unsigned int k = 0; k < dim_-1; k++ ) {
                os << vec_[k] << ", ";
            }
            os << vec_[dim_-1] << ")" << std::endl;
        }
    
        // scale vector with a constant
        void scale( double factor ) {
            // leave that to students
        }
    
        // add two vectors together (that's actually a little bit tricky, due to the question "where to put the result?"
        // for the moment leave it with adding another vector to the one on which the method is called;
        // let us try the following, and determine, why it will fail ;-)
        void add( VectorClass other ) {

            // make sure that input vector has correct length
            assert( other.getDim() == dim_ );
            for( unsigned int k = 0; k < dim_; k++ ) {
                vec_[k] += other[k+1];
            }
            //for( unsigned int k = 1; k <= dim_; k++ ) {
            //    this->operator[](k) += other[k];
            //}
        }
    
    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector

};

// Modify driver a little bit
int main() {

    const unsigned int dim = 10;
  
    // set up 1st vector
    VectorClass myVec( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      myVec[ idx ] = static_cast<double>( dim - idx + 1u );
    }
    myVec.print( std::cout );
    
    // set up 2nd vector
    VectorClass second( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      second[ idx ] = static_cast<double>( idx );
    }
    second.print( std::cout );
    
    // add the 2nd to the 1st
    myVec.add( second );
    myVec.print();
}

Overwriting VectorClass.cpp


In [32]:
!g++ -g VectorClass.cpp

In [33]:
!./a.out

An instance of VectorClass was generated. dim_ = 10
(10, 9, 8, 7, 6, 5, 4, 3, 2, 1)
An instance of VectorClass was generated. dim_ = 10
(1, 2, 3, 4, 5, 6, 7, 8, 9, 10)
An instance of VectorClass was destroyed and 80 bytes freed.
(11, 11, 11, 11, 11, 11, 11, 11, 11, 11)
free(): double free detected in tcache 2
Aborted (core dumped)


**Note**: The adding itself seems to have worked correctly, but somehow we still have a problem. So what's wrong here?

The answer to this is multifaceted:
- Our implementation of *add()* used **call-by-copy**
- Since we pass an object, its **copy constructor** is invoked
- We haven't implemented one, but the compiler did automatically (thank's for that ;-)
- Thus, the copy we get of **other** is a **flat** one!

***
We can check on that by making the destructor tell us which block it is going to deallocate and run our code through valgrind:
***
**==> valgrind ./a.out**
<div>
==28488== Memcheck, a memory error detector</br>
==28488== Copyright (C) 2002-2017, and GNU GPL'd, by Julian Seward et al.</br>
==28488== Using Valgrind-3.14.0 and LibVEX; rerun with -h for copyright info</br>
==28488== Command: ./a.out</br>
==28488== </br>
An instance of VectorClass was generated. dim_ = 10</br>
(10, 9, 8, 7, 6, 5, 4, 3, 2, 1)</br>
An instance of VectorClass was generated. dim_ = 10</br>
(1, 2, 3, 4, 5, 6, 7, 8, 9, 10)</br>
<font color="red">Going to delete memory starting at address 0x4d9b150</font></br>
An instance of VectorClass was destroyed and 80 bytes freed.</br>
(11, 11, 11, 11, 11, 11, 11, 11, 11, 11)</br>
<font color="red">Going to delete memory starting at address 0x4d9b150</font></br>
==28488== Invalid free() / delete / delete[] / realloc()</br>
==28488==    at 0x483758B: operator delete[](void*) (in /usr/lib/x86_64-linux-gnu/valgrind/vgpreload_memcheck-amd64-linux.so)</br>
==28488==    by 0x109500: VectorClass::~VectorClass() (VectorClass3.cpp:30)</br>
==28488==    by 0x109341: main (VectorClass3.cpp:93)</br>
==28488==  Address 0x4d9b150 is 0 bytes inside a block of size 80 free'd</br>
==28488==    at 0x483758B: operator delete[](void*) (in /usr/lib/x86_64-linux-gnu/valgrind/vgpreload_memcheck-amd64-linux.so)</br>
==28488==    by 0x109500: VectorClass::~VectorClass() (VectorClass3.cpp:30)</br>
==28488==    by 0x109322: main (VectorClass3.cpp:100)</br>
==28488==  Block was alloc'd at</br>
==28488==    at 0x483650F: operator new[](unsigned long) (in /usr/lib/x86_64-linux-gnu/valgrind/vgpreload_memcheck-amd64-linux.so)</br>
==28488==    by 0x109450: VectorClass::VectorClass(unsigned int) (VectorClass3.cpp:15)</br>
==28488==    by 0x109291: main (VectorClass3.cpp:93)</br>
==28488== </br>
An instance of VectorClass was destroyed and 80 bytes freed.</br>
Going to delete memory starting at address 0x4d9ac80</br>
An instance of VectorClass was destroyed and 80 bytes freed.</br>
==28488== </br>
==28488== HEAP SUMMARY:</br>
==28488==     in use at exit: 0 bytes in 0 blocks</br>
==28488==   total heap usage: 4 allocs, 5 frees, 73,888 bytes allocated</br>
==28488== </br>
==28488== All heap blocks were freed -- no leaks are possible</br>
==28488== </br>
==28488== For counts of detected and suppressed errors, rerun with: -v</br>
==28488== ERROR SUMMARY: 1 errors from 1 contexts (suppressed: 0 from 0)</br>
</div>

Another way to check on this is to remove the automatic copy constructor

In [34]:
%%file VectorClass.cpp

#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( dim_ > 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = " << dim_ << std::endl;
        }

        // Don't allow the default constructor
        // [prior to C++11 you would solve this by making it private]
        VectorClass() = delete;

        // Don't allow the following default copy constructor either
        VectorClass( VectorClass &other ) = delete;
    
        // We need to implement a destructor to free the dynamic memory again,
        // otherwise we easily produce memory leaks
        ~VectorClass() {
            delete[] vec_;
            std::cout << "An instance of VectorClass was destroyed and "
                      << dim_ * sizeof(double)
                      << " bytes freed." << std::endl;
        }

        // provide access to the vector's dimension
        unsigned int getDim() { return dim_; }
    
        // overload the [] for accessing individual entries
        double& operator[] ( unsigned int index ){
            assert( index != 0 && index <= dim_ );
            return vec_[index-1];
        }

        // pretty print vector to given output stream (default will be std::cout)
        void print( std::ostream &os = std::cout ) {
            os << "(";
            for( unsigned int k = 0; k < dim_-1; k++ ) {
                os << vec_[k] << ", ";
            }
            os << vec_[dim_-1] << ")" << std::endl;
        }
    
        // scale vector with a constant
        void scale( double factor ) {
            // leave that to students
        }
    
        // add two vectors together (that's actually a little bit tricky, due to the question "where to put the result?"
        // for the moment leave it with adding another vector to the one on which the method is called;
        // let us try the following, and determine, why it will fail ;-)
        void add( VectorClass other ) {

            // make sure that input vector has correct length
            assert( other.getDim() == dim_ );
            // for( unsigned int k = 0; k < dim_; k++ ) {
            //     vec_[k] += other[k+1];
            // }
            for( unsigned int k = 1; k <= dim_; k++ ) {
                this->operator[](k) += other[k];
            }
        }
    
    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector

};

// Modify driver a little bit
int main() {

    const unsigned int dim = 10;
  
    // set up 1st vector
    VectorClass myVec( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      myVec[ idx ] = static_cast<double>( dim - idx + 1 );
    }
    myVec.print( std::cout );
    
    // set up 2nd vector
    VectorClass other( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      other[ idx ] = static_cast<double>( idx );
    }
    other.print( std::cout );
    
    // add the 2nd to the 1st
    myVec.add( other );
    myVec.print();
}

Overwriting VectorClass.cpp


In [35]:
!g++ VectorClass.cpp

VectorClass.cpp: In function ‘int main()’:
VectorClass.cpp:102:22: error: use of deleted function ‘VectorClass::VectorClass(VectorClass&)’
     myVec.add( other );
                      ^
VectorClass.cpp:27:9: note: declared here
         VectorClass( VectorClass &other ) = delete;
         ^~~~~~~~~~~
VectorClass.cpp:64:14: note:   initializing argument 1 of ‘void VectorClass::add(VectorClass)’
         void add( VectorClass other ) {
              ^~~


#### Solution?
How should we resolve the issue?
***
For the current case the best solution is to change the interface of our `add()` method to be

`void add( const VectorClass& other )`

The `const` is no must, but makes it clear to other programmers and the compiler that we are not going to change the object
other inside add().

In [1]:
#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( dim_ > 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = " << dim_ << std::endl;
        }

        // Don't allow the default constructor [prior to C++11 you would solve this by making it private]
        VectorClass() = delete;

        // Don't allow the following default copy constructor either
        VectorClass( VectorClass &other ) = delete;
    
        // We need to implement a destructor to free the dynamic memory again, otherwise we easily produce
        // memory leaks
        ~VectorClass() {
            delete[] vec_;
            std::cout << "An instance of VectorClass was destroyed and " << dim_ * sizeof(double)
                      << " bytes freed." << std::endl;
        }

        // provide access to the vector's dimension
        unsigned int getDim() { return dim_; }
    
        // overload the [] for accessing individual entries
        double& operator[] ( unsigned int index ){
            assert( index != 0 && index <= dim_ );
            return vec_[index-1];
        }

        // pretty print vector to given output stream (default will be std::cout)
        void print( std::ostream &os = std::cout ) {
            os << "(";
            for( unsigned int k = 0; k < dim_-1; k++ ) {
                os << vec_[k] << ", ";
            }
            os << vec_[dim_-1] << ")" << std::endl;
        }
    
        // scale vector with a constant
        void scale( double factor ) {
            // leave that to students
        }
    
        // add two vectors together (that's actually a little bit tricky, due to the question "where to put the result?"
        // for the moment leave it with adding another vector to the one on which the method is called.
    
        // let us try the following, and determine, why it will fail ;-)
        void add( const VectorClass& other ) {

            // make sure that input vector has correct length
            assert( other.getDim() == dim_ );
            // for( unsigned int k = 0; k < dim_; k++ ) {
            //     vec_[k] += other[k+1];
            // }
            for( unsigned int k = 1; k <= dim_; k++ ) {
                this->operator[](k) += other[k];
            }
        }
    
    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector

};

// Modify driver a little bit
int main() {

    const unsigned int dim = 10;
  
    // set up 1st vector
    VectorClass myVec( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      myVec[ idx ] = static_cast<double>( dim - idx + 1 );
    }
    myVec.print( std::cout );
    
    // set up 2nd vector
    VectorClass other( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      other[ idx ] = static_cast<double>( idx );
    }
    other.print( std::cout );
    
    // add the 2nd to the 1st
    myVec.add( other );
    myVec.print();
}

input_line_8:61:45: error: no viable overloaded operator[] for type 'const VectorClass'
                this->operator[](k) += other[k];
                                       ~~~~~^~
input_line_8:32:17: note: candidate function not viable: 'this' argument has type 'const VectorClass', but method is not marked const
        double& operator[] ( unsigned int index ){
                ^
input_line_8:71:13: error: function definition is not allowed here
 int main() {
            ^


Interpreter Error: 

***
Ah, okay. So the `const` was a good idea, but requires a little bit of extra work!

We need to implement a second version of the operator overloading that returns a const reference!

In [2]:
#include <iostream>
#include <cassert>

class VectorClass{
    
    public:
    
        // User should specify dimension at object creation
        VectorClass( unsigned int dim ) : dim_(dim) {
            
            // don't allow vectors with zero dimension
            assert( dim_ > 0 );

            // allocate memory (will throw an exception, if it fails)
            vec_ = new double[ dim_ ];
            
            // be talkative ;-)
            std::cout << "An instance of VectorClass was generated. dim_ = "
                      << dim_ << std::endl;
        }

        // Don't allow the default constructor
        // [prior to C++11 you would solve this by making it private]
        VectorClass() = delete;

        // Don't allow the following default copy constructor either
        VectorClass( VectorClass &other ) = delete;
    
        // We need to implement a destructor to free the dynamic memory again,
        // otherwise we easily produce memory leaks
        ~VectorClass() {
            delete[] vec_;
            std::cout << "An instance of VectorClass was destroyed and "
                      << dim_ * sizeof(double)
                      << " bytes freed." << std::endl;
        }

        // provide access to the vector's dimension
        unsigned int getDim() { return dim_; }
    
        // overload the [] for accessing individual entries
        double& operator[] ( unsigned int index ){
            assert( index != 0 && index <= dim_ );
            return vec_[index-1];
        }
    
        // overload the [] for accessing individual entries
        const double& operator[] ( unsigned int index ) {
            assert( index != 0 && index <= dim_ );
            return vec_[index-1];
        }
    
        // pretty print vector to given output stream (default will be std::cout)
        void print( std::ostream &os = std::cout ) {
            os << "(";
            for( unsigned int k = 0; k < dim_-1; k++ ) {
                os << vec_[k] << ", ";
            }
            os << vec_[dim_-1] << ")" << std::endl;
        }
    
        // scale vector with a constant
        void scale( double factor ) {
            // leave that to students
        }
    
        // add to vectors together (that's actually a little bit tricky, due to the question "where to put the result?"
        // for the moment leave it with adding another vector to the one on which the method is called;
        // let us try the following, and determine, why it will fail ;-)
        void add( const VectorClass& other ) {

            // make sure that input vector has correct length
            assert( other.getDim() == dim_ );
            // for( unsigned int k = 0; k < dim_; k++ ) {
            //     vec_[k] += other[k+1];
            // }
            for( unsigned int k = 1; k <= dim_; k++ ) {
                this->operator[](k) += other[k];
            }
        }
    
    private:
        unsigned int dim_;   // dimension of vector
        double* vec_;        // entries of vector

};

// Modify driver a little bit
int main() {

    const unsigned int dim = 10;
  
    // set up 1st vector
    VectorClass myVec( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      myVec[ idx ] = static_cast<double>( dim - idx + 1 );
    }
    myVec.print( std::cout );
    
    // set up 2nd vector
    VectorClass other( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      other[ idx ] = static_cast<double>( idx );
    }
    other.print( std::cout );
    
    // add the 2nd to the 1st
    myVec.add( other );
    myVec.print();
}

input_line_10:41:23: error: functions that differ only in their return type cannot be overloaded
        const double& operator[] ( unsigned int index ) {
              ~~~~~~~ ^
input_line_10:35:17: note: previous definition is here
        double& operator[] ( unsigned int index ){
        ~~~~~~~ ^
input_line_10:15:23: error: use of overloaded operator '<<' is ambiguous (with operand types
      'basic_ostream<char, std::char_traits<char> >' and 'unsigned int')
                      << dim_ << std::endl;
                      ^  ~~~~
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostream:166:7: note: candidate function
      operator<<(long __n)
      ^
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostream:174:7: note: candidate function
      operator<<(bool __n)
      ^
/home/mohr/local/miniconda3/envs/cl

input_line_10:50:20: error: use of overloaded operator '<<' is ambiguous (with operand types 'std::ostream'
      (aka 'basic_ostream<char>') and 'double')
                os << vec_[k] << ", ";
                ~~ ^  ~~~~~~~
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostream:166:7: note: candidate function
      operator<<(long __n)
      ^
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostream:174:7: note: candidate function
      operator<<(bool __n)
      ^
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostream:178:7: note: candidate function
      operator<<(short __n);
      ^
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostr

        double& operator[] ( unsigned int index ){
                ^
input_line_10:80:13: error: function definition is not allowed here
 int main() {
            ^
In file included from input_line_5:1:
In file included from /home/mohr/local/miniconda3/envs/cling/include/xeus/xinterpreter.hpp:17:
In file included from /home/mohr/local/miniconda3/envs/cling/include/xeus/xcomm.hpp:19:
In file included from /home/mohr/local/miniconda3/envs/cling/include/nlohmann/json.hpp:42:
In file included from /home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/iterator:64:
/home/mohr/local/miniconda3/envs/cling/bin/../lib/gcc/x86_64-conda-linux-gnu/9.3.0/../../../../x86_64-conda-linux-gnu/include/c++/9.3.0/ostream:568:8: error: no member named 'setstate' in 'std::basic_ostream<char>'
        __out.setstate(ios_base::badbit);
        ~~~~~ ^
input_line_10:14:23: note: in instantiation of function template specialization

Interpreter Error: 

Shoot, we have a problem with the **signature** now!

But, fortunately, there is a way out of this:
- We can tell the compiler that a member function does not alter its object! This will also be part of the signature. So we can implement our overloading as
`const double& operator[] ( unsigned int index ) const`
- We might want to do this also for any other member function that does not change the object, like e.g. `print()`

Additionally, let us make add() nicer by using the fact that objects of the same class have access to their private data members!

If we do both, we end up with the final version:

In [1]:
#include <iostream>
#include <cassert>

class VectorClass {
    
public:
    
  // User should specify dimension at object creation
  VectorClass( unsigned int dim ) : dim_(dim) {
            
    // don't allow vectors with zero dimension
    assert( dim_ > 0 );

    // allocate memory (will throw an exception, if it fails)
    vec_ = new double[ dim_ ];
            
    // be talkative ;-)
    std::cout << "An instance of VectorClass was generated. dim_ = " 
              << dim_ << std::endl;
  }

  // Don't allow the default constructor
  // [prior to C++11 you would solve this by making it private]
  VectorClass() = delete;

  // Don't allow the following default copy constructor either    
  VectorClass( VectorClass &other ) = delete;
 
  // We need to implement a destructor to free the dynamic memory again,
  // otherwise we easily produce memory leaks
  ~VectorClass() {
    std::cout << "Going to delete memory starting at address "
              << vec_ << std::endl;
          
    delete[] vec_;
    std::cout << "An instance of VectorClass was destroyed and "
              << dim_ * sizeof(double)
              << " bytes freed." << std::endl;
  }

  // provide access to the vector's dimension
  unsigned int getDim() const { return dim_; }
    
  // overload the [] for accessing individual entries
  double& operator[] ( unsigned int index ) {
    assert( index != 0 && index <= dim_ );
    return vec_[index-1];
  }

  const double& operator[] ( unsigned int index ) const {
    assert( index != 0 && index <= dim_ );
    return vec_[index-1];
  }

  // pretty print vector to given output stream (default will be std::cout)
  void print( std::ostream &os = std::cout ) const {
    os << "(";
    for( unsigned int k = 0; k < dim_-1; k++ ) {
      os << vec_[k] << ", ";
    }
    os << vec_[dim_-1] << ")" << std::endl;
  }
    
  // scale vector with a constant
  void scale( double factor ) {
    // leave that to students
  }
    
  // add to vectors together (that's actually a little bit tricky,
  // due to the question "where to put the result?";
  // for the moment leave it with adding another vector to the one on which
  // the method is called.
  void add( const VectorClass& other ) {

    // make sure that input vector has correct length
    assert( other.dim_ == dim_ );
    for( unsigned int k = 0; k < dim_; k++ ) {
        vec_[k] += other.vec_[k];
    }
  }
    
private:
  unsigned int dim_;   // dimension of vector
  double* vec_;        // entries of vector

};

In [2]:
int main() {

    const unsigned int dim = 10;
  
    // set up 1st vector
    VectorClass myVec( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      myVec[ idx ] = static_cast<double>( dim - idx + 1 );
    }
    myVec.print( std::cout );
    
    // set up 2nd vector
    VectorClass other( dim );
    for( unsigned int idx = 1; idx <= dim; idx ++ ) {
      other[ idx ] = static_cast<double>( idx );
    }
    other.print( std::cout );
    
    // add the 2nd to the 1st
    myVec.add( other );
    myVec.print();
}

In [3]:
main();

An instance of VectorClass was generated. dim_ = 10
(10, 9, 8, 7, 6, 5, 4, 3, 2, 1)
An instance of VectorClass was generated. dim_ = 10
(1, 2, 3, 4, 5, 6, 7, 8, 9, 10)
(11, 11, 11, 11, 11, 11, 11, 11, 11, 11)
Going to delete memory starting at address 0x561e481ef440
An instance of VectorClass was destroyed and 80 bytes freed.
Going to delete memory starting at address 0x561e480f55f0
An instance of VectorClass was destroyed and 80 bytes freed.


***
#### Separating Implementation and Interface

- Assume that we have the definition of a `class A` in one source file and want to use the class in another source file `B.cpp`.
- For this the compiler needs to known at least that `class A` exists:  
  This can be accomplished by a **forward declaration** of the form  `class A;`
- However, if we also want to access data or function members of A, the compiler needs further info.
- There are three possibilities:
  1. Put the complete definition of A into a header file `A.hpp` and include that into the source file `B.cpp`
  1. Split up the declaration of the member functions and their implementation into two parts. A file `A.hpp` with the class declaration and a file `A.cpp` with the implementation of the member functions.
  1. Use a combination of both, e.g. to allow inlining of certain short methods.
- Each of the approaches has pros and cons. So the decision depends on the concrete scenario.
***
Brief example on the splitting approach:

In [4]:
%%file splitA.hpp

#include <string>

class A {

  std::string name_;

  public:
  void setName( const char* name );
  void printName();

};

Overwriting splitA.hpp


In [5]:
%%file splitA.cpp

// Necessary, because otherwise compiler does not know a class A and a member function setName exists
#include "splitA.hpp"

// Need to prefix the member function name with the class name
void A::setName( const char* name ) {
  name_ = name;
}

Overwriting splitA.cpp


In [6]:
%%file splitB.cpp

#include "splitA.hpp"

int main( void ) {

  A obj;
  obj.setName( "An object" );

  // Note: We have not implemented A::printName();
  //       However, if it is not used, that's not an issue.
  // obj.printName();
}

Overwriting splitB.cpp


In [7]:
!g++ splitA.cpp splitB.cpp
./a.out